In [6]:
import pandas as pd
import json
from phoenix.client import Client

# Load the existing spans
spans_df = Client().spans.get_spans_dataframe(project_name="default", start_time="2025-10-23")

In [7]:
# Load the source of truth
dataset_df = pd.read_json("../data/metadata.jsonl", lines=True)

In [8]:
# Filter by root agents
agents_df = spans_df[(spans_df.span_kind == 'AGENT') & (spans_df.parent_id.isna()) & (spans_df.status_code == 'OK')]

In [9]:
# Retrieve the right question and add the answer
agents_df["task"] = agents_df["attributes.input.value"].apply(json.loads).apply(lambda x : x["task"]).str.replace(r'\s*The mentionned file can be downloaded from.*$', '', regex=True)
agents_merged_df = pd.merge(agents_df,dataset_df,how="left",left_on="task", right_on="Question")

/var/folders/pj/v1zrqj1d10x9_1rd2njh_r_r0000gn/T/ipykernel_35129/3107371246.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  agents_df["task"] = agents_df["attributes.input.value"].apply(json.loads).apply(lambda x : x["task"]).str.replace(r'\s*The mentionned file can be downloaded from.*$', '', regex=True)


In [10]:
from phoenix.evals.evaluators import bind_evaluator, async_evaluate_dataframe
from evaluators import conciseness_evaluator
from scorer import question_scorer_wrapper as question_scorer

# Define the evaluator
conciseness_evaluator = bind_evaluator(evaluator=conciseness_evaluator, input_mapping={ "output": "attributes.output.value", "expected": "Final answer"})
question_scorer_eval = bind_evaluator(evaluator=question_scorer, input_mapping={ "output": "attributes.output.value", "expected": "Final answer"})
results_df = await async_evaluate_dataframe(agents_merged_df, evaluators=[conciseness_evaluator, question_scorer_eval])


Evaluating <code>
page_content_log = visit_webpage(url="https://en.wikipedia.org/wiki/Wikipedia:Featured_article_candidates/Featured_log/November_2016")
print(page_content_log)
</code>
Calling tools:
[{'id': 'call_8', 'type': 'function', 'function': {'name': 'python_interpreter', 'arguments': 'page_content_log = visit_webpage(url="https://en.wikipedia.org/wiki/Wikipedia:Featured_article_candidates/Featured_log/November_2016")\nprint(page_content_log)'}}] as a string.
Evaluating right as a string.
Evaluating The provided problem requires visual inspection of a chess board image which I cannot access in the current environment. To properly solve this, one would need to analyze the specific piece positions in the image to identify a forcing tactical sequence leading to a guaranteed win for Black. Standard approaches would involve identifying forced captures, mating patterns, or immediate tactical threats that Black can execute on their turn. as a string.
Evaluating right as a string.
Eval

/Users/romainfayoux/Documents/Programmation/Final_Assignment_Template/eval/scorer.py:61: UserWarning: Answer lists have different lengths, returning False.
  warnings.warn(


Evaluating Given the issues accessing the specific Wikipedia page directly, I will use an alternative approach to find the information. I'll search for the specific Featured Article about a dinosaur promoted in November 2016 and then look for its nomination details.

Let's start by searching for the specific Featured Article about a dinosaur promoted in November 2016.

<code>
# Perform a web search to find the specific Featured Article about a dinosaur promoted in November 2016
search_results = web_search(query="Featured Article dinosaur promoted November 2016")
print(search_results)
</code>
Calling tools:
[{'id': 'call_8', 'type': 'function', 'function': {'name': 'python_interpreter', 'arguments': '# Perform a web search to find the specific Featured Article about a dinosaur promoted in November 2016\nsearch_results = web_search(query="Featured Article dinosaur promoted November 2016")\nprint(search_results)'}}] as a string.
Evaluating d5 as a string.
Evaluating right as a string.
Eva

In [11]:
results_df["conciseness"] = results_df.conciseness_evaluator_score.apply(json.loads).apply(lambda x : x["label"])
results_df["question_scorer"] = results_df.question_scorer_score.apply(json.loads).apply(lambda x : x["score"])
results_df["agent_type"] = results_df["attributes.smolagents"].apply(lambda x : "multi_agent" if "managed_agents" in x else "llm_agent")
results_filtered_df = results_df[["name", "span_kind", "start_time", "context.span_id", "context.trace_id","attributes.output.value", "task_id", "Question", "Final answer", "agent_type", "conciseness_evaluator_score", "question_scorer_score", "conciseness", "question_scorer"]]

In [12]:
# Upload results
import numpy as np
from phoenix.evals.utils import to_annotation_dataframe

annotation_df = to_annotation_dataframe(results_filtered_df)
annotation_df = annotation_df.replace({np.nan: None})
Client().spans.log_span_annotations_dataframe(dataframe=annotation_df)


/Users/romainfayoux/Documents/Programmation/Final_Assignment_Template/.venv/lib/python3.12/site-packages/phoenix/evals/utils.py:367: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  result_df = pd.concat(result_dfs, ignore_index=True)
